In [2]:
import pandas as pd
import main
from conversion import points_to_smooth_lines
from conversion_v2 import points_to_smooth_lines_fast
import plotly.graph_objects as go
from buffer import identify_matching
import glob


These are the imports required for running this algorithm, and creating the map. If a user does not want to create the map, then only the pandas and main modules are needed. The user also does not have to use any of these conversion modules if they have their own.

In [ ]:
##########################
# LOADING DATA
##########################

In [ ]:
# ASTD Dataset after original conditioning 

df_astd_original = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/grouped-months/all_months_1day.csv', sep=',')




Processing 2776664 records
Data sample after cleaning:
  Date range: 2019-01-31 00:00:00 to 2019-12-01 23:59:57
  Ship types: ['fishing vessels' 'passenger ships' 'general cargo ships'
 'other activities' 'ro-ro cargo ships' 'offshore supply ships'
 'crude oil tankers' 'bulk carriers' 'refrigerated cargo ships'
 'oil product tankers' 'other service offshore vessels' 'chemical tankers'
 'cruise ships' 'container ships' 'gas tankers']
  Unique ships: 6832
Creating segments for 6832 unique shipids
Created 6832 segments
Sample segment: fishing vessels|iceland|fs ice class 1c|< 1000 gt
Found 6832 segments across 12 time periods
Created 5434 tracks


This is the preprocessed astd DataFrame. It then gets run through the main algorithm build_track_table. buiild_track_table outputs a table with the month, segment_id and track_id

In [ ]:
# automate this part 
# somehow be able to call specific months each time

df_jul_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201907.csv', sep=';')
df_aug_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201908.csv', sep=';')
df_sep_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201909.csv', sep=';')
df_oct_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201910.csv', sep=';')
df_nov_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201911.csv', sep=';')
df_dec_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201912.csv', sep=';')

/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_36634/1481213226.py:1: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  df_jul_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201907.csv', sep=';')
/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_36634/1481213226.py:2: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  df_aug_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201908.csv', sep=';')
/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_36634/1481213226.py:3: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  df_sep_astd = pd.read_csv('/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019/ASTD_area_level3_201909.csv', sep=';')
/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipyker

These are the original ASTD datasets. They have not been preprocessed. These are required to find the ships for creating a map.

In [10]:
# GFW DATA

def load_month_data(year, month, base_path):
    pattern = f"{base_path}/mmsi-daily-csvs-10-v3-{year}-{month:02d}-*.csv"
    files = glob.glob(pattern)
    if files:
        return pd.concat([pd.read_csv(file) for file in files], ignore_index=True)
    else:
        print(f"No files found for {year}-{month:02d}")
        return pd.DataFrame()

# Load different months
base_path = "/Users/willponczak/Desktop/QC2025/data/gfw/ais-apparent-fishing-effort/mmsi-daily-csvs-10-v3-2019"

df_jan_gfw = load_month_data(2019, 1, base_path)  
df_feb_gfw = load_month_data(2019, 2, base_path)   
df_mar_gfw = load_month_data(2019, 3, base_path)  
df_apr_gfw = load_month_data(2019, 4, base_path)  
df_may_gfw = load_month_data(2019, 5, base_path)  
df_jun_gfw = load_month_data(2019, 6, base_path)  
df_jul_gfw = load_month_data(2019, 7, base_path)  
df_aug_gfw = load_month_data(2019, 8, base_path)  
df_sep_gfw = load_month_data(2019, 9, base_path)  
df_oct_gfw = load_month_data(2019, 10, base_path)  
df_nov_gfw = load_month_data(2019, 11, base_path)  
df_dec_gfw = load_month_data(2019, 12, base_path)  

In [ ]:
############################
# RUNNING MAIN ALGORITHM
############################

This is the GFW data. This was only apart of our verification process, so a user would not need to import these datasets unless they wanted to.

In [ ]:
# Running orig df through algorithm
track_table = main.build_track_table(df_astd_original)

track_info = track_table[track_table['track_id'] == 'track_3566']
track_info

month  segment_id    track_id
4482  2019-07         403  track_3566
4483  2019-08         626  track_3566
4484  2019-09         742  track_3566
4485  2019-10         229  track_3566
4486  2019-11         216  track_3566
4487  2019-12         193  track_3566

In [5]:
import pandas as pd
import os

# Configuration
base_path = '/Users/willponczak/Desktop/QC2025/data/astd/complete_data/2019'
year = '2019'

# Get the months that are actually used in track_info
months_needed = sorted(track_info['month'].unique())
print(f"Months needed from track_info: {months_needed}")

# Month name mapping
month_name_mapping = {
    '2019-01': 'jan', '2019-02': 'feb', '2019-03': 'mar', '2019-04': 'apr',
    '2019-05': 'may', '2019-06': 'jun', '2019-07': 'jul', '2019-08': 'aug',
    '2019-09': 'sep', '2019-10': 'oct', '2019-11': 'nov', '2019-12': 'dec'
}

# Load CSV files ONLY for the months that appear in track_info
datasets = {}
filtered_datasets = {}

for month in months_needed:
    if month in month_name_mapping:
        month_name = month_name_mapping[month]
        
        # Construct filename
        month_num = month.split('-')[1]  # Extract '07' from '2019-07'
        filename = f'ASTD_area_level3_{year}{month_num}.csv'
        filepath = os.path.join(base_path, filename)
        
        # Check if file exists before trying to load it
        if os.path.exists(filepath):
            print(f"Loading {filename}...")
            month_df = pd.read_csv(filepath, sep=';')
            datasets[f'df_{month_name}_astd'] = month_df
            
            # Create filtered version (just drop NaN for now)
            filtered_df = month_df.dropna()
            filtered_datasets[f'df_{month_name}_filtered_astd_3566'] = filtered_df
            
            print(f"{month_name.capitalize()}: {len(month_df)} total rows, {len(filtered_df)} after dropna")
        else:
            print(f"Warning: File {filename} not found!")
    else:
        print(f"Warning: No month name mapping for {month}")

# Create individual variables
for month in months_needed:
    if month in month_name_mapping and month_name_mapping[month] in [key.split('_')[1] for key in datasets.keys()]:
        month_name = month_name_mapping[month]
        globals()[f'df_{month_name}_astd'] = datasets[f'df_{month_name}_astd']
        globals()[f'df_{month_name}_filtered_astd_3566'] = filtered_datasets[f'df_{month_name}_filtered_astd_3566']

# Show what segment_ids are available for each loaded month
print("\nSegment IDs by month:")
for month in months_needed:
    if month in month_name_mapping:
        month_name = month_name_mapping[month]
        dataset_key = f'df_{month_name}_astd'
        if dataset_key in datasets:
            month_data = datasets[dataset_key]
            if 'segment_id' in month_data.columns:
                segment_ids = sorted(month_data['segment_id'].unique())
                print(f"{month}: {segment_ids}")
            else:
                print(f"{month}: No 'segment_id' column found")

print(f"\nDatasets created: {list(datasets.keys())}")
print(f"Filtered datasets created: {list(filtered_datasets.keys())}")

Months needed from track_info: ['2019-07', '2019-08', '2019-09', '2019-10', '2019-11', '2019-12']
Loading ASTD_area_level3_201907.csv...


/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_2529/1307999835.py:35: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  month_df = pd.read_csv(filepath, sep=';')


Jul: 21134448 total rows, 4179180 after dropna
Loading ASTD_area_level3_201908.csv...


/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_2529/1307999835.py:35: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  month_df = pd.read_csv(filepath, sep=';')


Aug: 20824974 total rows, 4151687 after dropna
Loading ASTD_area_level3_201909.csv...


...

Oct: 17721130 total rows, 3420555 after dropna
Loading ASTD_area_level3_201911.csv...


/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_2529/1307999835.py:35: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  month_df = pd.read_csv(filepath, sep=';')


Nov: 18647052 total rows, 3697680 after dropna
Loading ASTD_area_level3_201912.csv...


/var/folders/9d/bphw52wd7fngbyw4fdd0280h0000gp/T/ipykernel_2529/1307999835.py:35: DtypeWarning: Columns (3,5) have mixed types. Specify dtype option on import or set low_memory=False.
  month_df = pd.read_csv(filepath, sep=';')


Dec: 18772772 total rows, 3912124 after dropna

Segment IDs by month:
2019-07: No 'segment_id' column found
2019-08: No 'segment_id' column found
2019-09: No 'segment_id' column found
2019-10: No 'segment_id' column found
2019-11: No 'segment_id' column found
2019-12: No 'segment_id' column found

Datasets created: ['df_jul_astd', 'df_aug_astd', 'df_sep_astd', 'df_oct_astd', 'df_nov_astd', 'df_dec_astd']
Filtered datasets created: ['df_jul_filtered_astd_3566', 'df_aug_filtered_astd_3566', 'df_sep_filtered_astd_3566', 'df_oct_filtered_astd_3566', 'df_nov_filtered_astd_3566', 'df_dec_filtered_astd_3566']


This is the track being used in the example. track_info becomes a table with only rows containing track_3566 in the track_id column. I then print it out to see which months and segment_id I need to get from the ASTD data.

In [ ]:
##############################
# FILTERING DATA
##############################

In [ ]:
# Filter each month for the specific shipid

#Automate this part.

df_jul_filtered_astd_3566 = df_jul_astd[df_jul_astd['shipid'] == 403].dropna()
df_aug_filtered_astd_3566 = df_aug_astd[df_aug_astd['shipid'] == 626].dropna()
df_sep_filtered_astd_3566 = df_sep_astd[df_sep_astd['shipid'] == 742].dropna()
df_oct_filtered_astd_3566 = df_oct_astd[df_oct_astd['shipid'] == 229].dropna()
df_nov_filtered_astd_3566 = df_nov_astd[df_nov_astd['shipid'] == 216].dropna()
df_dec_filtered_astd_3566 = df_dec_astd[df_dec_astd['shipid'] == 193].dropna()

print(f"Jul: {len(df_jul_filtered_astd_3566)}")
print(f"Aug: {len(df_aug_filtered_astd_3566)}")
print(f"Sep: {len(df_sep_filtered_astd_3566)}")
print(f"Oct: {len(df_oct_filtered_astd_3566)}")
print(f"Nov: {len(df_nov_filtered_astd_3566)}")
print(f"Dec: {len(df_dec_filtered_astd_3566)}")



# Combine them
df_filtered = pd.concat([df_jul_filtered_astd_3566, df_aug_filtered_astd_3566, df_sep_filtered_astd_3566,
                               df_oct_filtered_astd_3566, df_nov_filtered_astd_3566, df_dec_filtered_astd_3566], ignore_index=True)

Jul: 13297
Aug: 13353
Sep: 13052
Oct: 11099
Nov: 13169
Dec: 13060


In [6]:
df_filtered = pd.concat([df_jul_filtered_astd_3566, df_aug_filtered_astd_3566, df_sep_filtered_astd_3566,
                               df_oct_filtered_astd_3566, df_nov_filtered_astd_3566, df_dec_filtered_astd_3566], ignore_index=True)

In [14]:
df_filtered

shipid        date_time_utc    flagname               iceclass  \
0            403  2019-07-13 04:26:15     Iceland        FS Ice Class 1C   
1            403  2019-07-13 18:40:36     Iceland        FS Ice Class 1C   
2            403  2019-07-13 13:40:46     Iceland        FS Ice Class 1C   
3            403  2019-07-13 12:16:47     Iceland        FS Ice Class 1C   
4            403  2019-07-13 03:51:16     Iceland        FS Ice Class 1C   
...          ...                  ...         ...                    ...   
23298349    2151  2019-12-15 00:18:24     Estonia  FS Ice Class 1A Super   
23298350    8844  2019-12-15 11:48:04      Latvia        FS Ice Class 1C   
23298351    9702  2019-12-15 05:18:30  Luxembourg        FS Ice Class 1A   
23298352    9303  2019-12-15 22:34:48       Malta        FS Ice Class 1C   
23298353    1852  2019-12-15 14:37:58      Russia        FS Ice Class 1C   

                     astd_cat    sizegroup_gt  fuelquality  fuelcons  \
0             Fishing vessels       < 1000 GT            0  0.001224   
1             Fishing vessels       < 1000 GT            0  0.000812   
2             Fishing vessels       < 1000 GT            0  0.000136   
3             Fishing vessels       < 1000 GT            0  0.000880   
4             Fishing vessels       < 1000 GT            0  0.000914   
...                       ...             ...          ...       ...   
23298349      Passenger ships   10000 - 24999            2  0.018184   
23298350  General cargo ships  1000 - 4999 GT            1  0.000951   
23298351  General cargo ships  1000 - 4999 GT            1  0.020640   
23298352        Bulk carriers   10000 - 24999            3  0.009128   
23298353      Fishing vessels  1000 - 4999 GT            0  0.007264   

                co       co2  ...   blackcarbon  organiccarbon  oilbilgewater  \
0         0.000009  0.003879  ...  2.202000e-07   7.439000e-07   6.400000e-09   
1         0.000006  0.002575  ...  1.462000e-07   4.939000e-07   4.200000e-09   
2         0.000001  0.000431  ...  2.450000e-08   8.270000e-08   7.000000e-10   
3         0.000007  0.002791  ...  1.585000e-07   5.352000e-07   4.600000e-09   
4         0.000007  0.002898  ...  1.646000e-07   5.559000e-07   4.800000e-09   
...            ...       ...  ...           ...            ...            ...   
23298349  0.000135  0.058123  ...  3.273166e-06   1.105603e-05   3.128472e-09   
23298350  0.000007  0.003013  ...  1.710993e-07   5.779354e-07   1.335503e-08   
23298351  0.000153  0.065428  ...  3.715172e-06   1.254903e-05   2.508681e-08   
23298352  0.000068  0.029189  ...  1.643026e-06   5.549775e-06   7.260417e-09   
23298353  0.000054  0.023027  ...  1.307504e-06   4.416458e-06   6.168403e-08   

          blackwater  greywater   garbage  dist_nextpoint  sec_nextpoint  \
0           0.000417   0.003083  0.000000        2.355925            360   
1           0.000277   0.002047  0.000000        1.873214            239   
2           0.000046   0.000343  0.000000        1.961694             40   
3           0.000300   0.002218  0.000000        2.106996            259   
4           0.000311   0.002304  0.000000        3.127784            269   
...              ...        ...       ...             ...            ...   
23298349    0.051528   0.169306  0.001546      405.477000             53   
23298350    0.000576   0.004263  0.000035        0.933000            181   
23298351    0.001082   0.008008  0.000065     1664.578000            340   
23298352    0.000297   0.002195  0.000018      241.116000             41   
23298353    0.008128   0.026706  0.000174        1.358000            836   

          longitude   latitude  
0        -23.703354  64.895910  
1        -23.703373  64.895935  
2        -23.703468  64.895940  
3        -23.703396  64.895930  
4        -23.703348  64.895900  
...             ...        ...  
23298349  20.682000  59.650665  
23298350  20.346865  63.700775  
23298351  20.857416  63.551610  
23298352   9.294

In the first part of this, I filter each ASTD dataset so they only contain the specific ship that we want, and I assign it to a new variable. I then print how many rows of data each ship has. This step is not necessary for running the algorithm, or creating the map. It only helps the user get an idea of how much data they are working with. The last part of this cell is concatenating all of the filtered datasets into a single DataFrame that can be used to create a map.

In [11]:
track_3566_gfw = pd.concat([df_jul_gfw, df_aug_gfw, df_sep_gfw, df_oct_gfw, df_nov_gfw, df_dec_gfw])

Here, the GFW data for the relating months are also concatenated. This is a must for our verification process, but a user can completely skip this part.

In [ ]:
###############################
# RUNNING MATCHING ALGORITHM
###############################

In [ ]:
# del 

import gc

gc.collect()


In [ ]:
# This created the buffer around every nth point

mmsi_list = identify_matching(df_filtered, track_3566_gfw, 5000)

ASTD rows: 23298354, GFW rows: 29499936


: 

This cell runs a function from another file to automatically search for mmsi(s) which match the identified track_id. It uses both the filtered ASTD data, and the GFW data. This step is not necessary to create a map solely based on the ASTD data. It is only required for the verification process.

In [9]:
track_3566_df = track_3566_gfw[track_3566_gfw['mmsi'].isin(mmsi_list)]

track_3566_specific = points_to_smooth_lines(track_3566_df)

This cell takes all of the potential matching mmsi(s) from the mmsi_list and then runs them through a point-to-lines algorithm so we can visually identify which mmsi is a match. This is not a necessary step for creating a map with only ASTD data. It is only necessary for the verification process.

In [ ]:
###########################
# MAP VISUALIZATION
###########################

In [10]:
# Create the map figure
fig = go.Figure()

# Add tracks from df (precise coordinates)
for ship_id in df_filtered['shipid'].unique():
    ship_data = df_filtered[df_filtered['shipid'] == ship_id].sort_values('date_time_utc')
    fig.add_trace(go.Scattermapbox(
        lat=ship_data['latitude'],
        lon=ship_data['longitude'],
        mode='markers',
        name=f'ASTD - {ship_id}',
        line=dict(width=2),
        customdata=ship_data[["date_time_utc", "shipid"]].values,
        hovertemplate="date: %{customdata[0]} id:%{customdata[1]}",
    ))

# Add tracks from df_jan_feb_gfw_specific_mmsi_smooth (grid cells)
for mmsi in track_3566_df['mmsi'].unique():
    mmsi_data = track_3566_df[track_3566_df['mmsi'] == mmsi].sort_index()
    fig.add_trace(go.Scattermapbox(
        lat=mmsi_data['cell_ll_lat'],  # or whatever your lat column is
        lon=mmsi_data['cell_ll_lon'],  # or whatever your lon column is
        mode='lines',
        name=f'GFW - {mmsi}',
        line=dict(width=2),
        customdata=mmsi_data[["date", "mmsi"]].values,
        hovertemplate="date: %{customdata[0]} id:%{customdata[1]}",
    ))

# Update layout
fig.update_layout(
    mapbox_style="open-street-map",
    height=600,
    margin={"r":0,"t":0,"l":0,"b":0},
    legend=dict(
        x=1,           # Right side (1 = far right, 0 = far left)
        y=0.5,           # Bottom (0 = bottom, 1 = top)
        xanchor='right',  # Anchor the legend box to its right edge
        yanchor='bottom'  # Anchor the legend box to its bottom edge
    )
)

fig.show()

This is where the map is created. The first block takes the filtered ASTD data and shows that on the map, which shows a visualization of the ship track identified by the main algorithm. The second block is for GFW data, and is only required for the verification process. A user could completely delete this block of code if they were not using the GFW dataset. The last block is for configuration of the map. This can be edited and played around with by the user.